In [0]:
from pyspark.sql.functions import col
from pyspark.ml.feature import Imputer

spark_dr = spark.read.csv("dbfs:/FileStore/tables/data_merged_A2.csv",header=True)

spark_dr = spark_dr.drop("customerID")

spark_dr = spark_dr.withColumn("tenure", col("tenure").cast("double")) \
       .withColumn("MonthlyCharges", col("MonthlyCharges").cast("double")) \
       .withColumn("TotalCharges", col("TotalCharges").cast("double"))
       
imputer = Imputer(inputCols=["TotalCharges"], outputCols=["TotalCharges"], strategy="mean")  # Or "median"

spark_dr = imputer.fit(spark_dr).transform(spark_dr)



In [0]:
trainDF, testDF = spark_dr.randomSplit([0.8, 0.2], seed=42)
print(trainDF.cache().count()) # Cache because accessing training data multiple times
print(testDF.count())

5698
1345


In [0]:
from pyspark.ml.feature import StringIndexer, OneHotEncoder

categoricalCols = [
    "gender",
    "SeniorCitizen",
    "Partner",
    "Dependents",
    "PhoneService",
    "MultipleLines",
    "InternetService",
    "OnlineSecurity",
    "OnlineBackup",
    "DeviceProtection",
    "TechSupport",
    "StreamingTV",
    "StreamingMovies",
    "Contract",
    "PaperlessBilling",
]

stringIndexer = StringIndexer(inputCols=categoricalCols, outputCols=[x + "Index" for x in categoricalCols]) 
encoder = OneHotEncoder(inputCols=stringIndexer.getOutputCols(), outputCols=[x + "OHE" for x in categoricalCols]) 

from pyspark.ml.feature import QuantileDiscretizer

# Apply QuantileDiscretizer to the TotalCharges column
discretizer = QuantileDiscretizer(numBuckets=4, inputCol="TotalCharges", outputCol="TotalChargesBucket")

# Fit the discretizer and transform the data
spark_dr = discretizer.fit(spark_dr).transform(spark_dr)

# Show the transformed data
spark_dr.select("TotalCharges", "TotalChargesBucket").show()

labelToIndex = StringIndexer(inputCol="Churn", outputCol="label")

+------------+------------------+
|TotalCharges|TotalChargesBucket|
+------------+------------------+
|       29.85|               0.0|
|      1889.5|               2.0|
|      108.15|               0.0|
|     1840.75|               2.0|
|      151.65|               0.0|
|       820.5|               1.0|
|      1949.4|               2.0|
|       301.9|               0.0|
|     3046.05|               2.0|
|     3487.95|               2.0|
|      587.45|               1.0|
|       326.8|               0.0|
|      5681.1|               3.0|
|      5036.3|               3.0|
|     2686.05|               2.0|
|     7895.15|               3.0|
|     1022.95|               1.0|
|     7382.25|               3.0|
|      528.35|               1.0|
|      1862.9|               2.0|
+------------+------------------+
only showing top 20 rows



In [0]:
stringIndexerModel = stringIndexer.fit(trainDF)
display(stringIndexerModel.transform(trainDF))

gender SeniorCitizen Partner Dependents tenure PhoneService MultipleLines InternetService OnlineSecurity OnlineBackup DeviceProtection TechSupport StreamingTV StreamingMovies Contract PaperlessBilling PaymentMethod MonthlyCharges TotalCharges Churn genderIndex SeniorCitizenIndex PartnerIndex DependentsIndex PhoneServiceIndex MultipleLinesIndex InternetServiceIndex OnlineSecurityIndex OnlineBackupIndex DeviceProtectionIndex TechSupportIndex StreamingTVIndex StreamingMoviesIndex ContractIndex PaperlessBillingIndex Female 0 No No 1.0 No No phone service DSL No No No No No No Month-to-month No Bank transfer (automatic) 25.25 25.25 No 1.0 0.0 0.0 0.0 1.0 2.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 No No phone service DSL No No No No No No Month-to-month No Electronic check 24.6 24.6 Yes 1.0 0.0 0.0 0.0 1.0 2.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 No No phone service DSL No No No No No No Month-to-month No Mailed check 24.4 24.4 No 1.0 0.0 0.0 0.0 1.0 2.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 No No phone service DSL No No No No No No Month-to-month No Mailed check 25.2 25.2 Yes 1.0 0.0 0.0 0.0 1.0 2.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 No No phone service DSL No No No No No No Month-to-month Yes Mailed check 24.9 24.9 No 1.0 0.0 0.0 0.0 1.0 2.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 Female 0 No No 1.0 No No phone service DSL No No No No No No Month-to-month Yes Mailed check 25.15 25.15 No 1.0 0.0 0.0 0.0 1.0 2.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 Female 0 No No 1.0 No No phone service DSL No No No No No Yes Month-to-month No Mailed check 35.05 35.05 Yes 1.0 0.0 0.0 0.0 1.0 2.0 1.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 1.0 Female 0 No No 1.0 No No phone service DSL No No No No Yes No Month-to-month Yes Electronic check 34.7 34.7 Yes 1.0 0.0 0.0 0.0 1.0 2.0 1.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 Female 0 No No 1.0 No No phone service DSL No No No No Yes No Month-to-month Yes Electronic check 35.75 35.75 Yes 1.0 0.0 0.0 0.0 1.0 2.0 1.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 Female 0 No No 1.0 No No phone service DSL No No No Yes No No Month-to-month No Mailed check 30.55 30.55 No 1.0 0.0 0.0 0.0 1.0 2.0 1.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 No No phone service DSL No Yes No No No No Month-to-month No Bank transfer (automatic) 29.95 29.95 Yes 1.0 0.0 0.0 0.0 1.0 2.0 1.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 No No phone service DSL Yes No No No No No Month-to-month No Mailed check 29.9 29.9 No 1.0 0.0 0.0 0.0 1.0 2.0 1.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 Yes No DSL No No No No No No Month-to-month No Bank transfer (automatic) 44.15 44.15 No 1.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 Yes No DSL No No No No No No Month-to-month No Credit card (automatic) 43.95 43.95 No 1.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 Yes No DSL No No No No No No Month-to-month No Electronic check 43.8 43.8 No 1.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 Yes No DSL No No No No No No Month-to-month No Electronic check 45.8 45.8 Yes 1.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 Yes No DSL No No No No No No Month-to-month No Mailed check 43.95 43.95 Yes 1.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 Yes No DSL No No No No No No Month-to-month No Mailed check 44.4 44.4 Yes 1.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 Yes No DSL No No No No No No Month-to-month No Mailed check 45.15 45.15 No 1.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 Yes No DSL No No No No No No Month-to-month No Mailed check 45.3 45.3 No 1.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 Yes No DSL No No No No No No Month-to-month No Mailed check 45.35 45.35 No 1.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 Female 0 No No 1.0 Yes 

In [0]:
from pyspark.ml.feature import VectorAssembler

assemblerInputs = [c + "OHE" for c in categoricalCols] + ["TotalChargesBucket"]
vecAssembler = VectorAssembler(inputCols=assemblerInputs, outputCol="features")

In [0]:
from pyspark.ml.classification import LogisticRegression
 
lr = LogisticRegression(featuresCol="features", labelCol="label", regParam=1.0)

In [0]:
from pyspark.ml import Pipeline
 
pipeline = Pipeline(stages=[
    labelToIndex,       
    stringIndexer,       
    encoder,
    discretizer,               
    vecAssembler,        
    lr                   
])

# Train the model using the training dataset
pipelineModel = pipeline.fit(trainDF)

# Apply the model to the test dataset
predDF = pipelineModel.transform(testDF)

In [0]:
display(predDF.select("features", "label", "prediction", "probability"))

features label prediction probability Map(vectorType -> sparse, length -> 25, indices -> List(1, 2, 3, 8, 9, 11, 13, 15, 17, 19, 21), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6446378037616957, 0.35536219623830434)) Map(vectorType -> sparse, length -> 25, indices -> List(1, 2, 3, 8, 9, 11, 13, 15, 17, 19, 21, 23), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 1.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6220356460729793, 0.37796435392702066)) Map(vectorType -> sparse, length -> 25, indices -> List(1, 2, 3, 8, 9, 11, 13, 15, 17, 19), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6918434612528463, 0.30815653874715365)) Map(vectorType -> sparse, length -> 25, indices -> List(1, 2, 3, 8, 9, 11, 14, 16, 17, 19, 21), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7255022218080446, 0.2744977781919554)) Map(vectorType -> sparse, length -> 25, indices -> List(1, 2, 3, 4, 5, 8, 9, 11, 13, 15, 17, 19, 21), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 1.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6472001142629059, 0.3527998857370941)) Map(vectorType -> sparse, length -> 25, indices -> List(1, 2, 3, 4, 5, 8, 9, 11, 13, 15, 17, 19, 21), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6472001142629059, 0.3527998857370941)) Map(vectorType -> sparse, length -> 25, indices -> List(1, 2, 3, 4, 5, 8, 9, 11, 13, 15, 17, 19, 21, 23), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6246660393434577, 0.37533396065654234)) Map(vectorType -> sparse, length -> 25, indices -> List(1, 2, 3, 4, 5, 8, 9, 11, 13, 15, 17, 19, 21, 23), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 1.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6246660393434577, 0.37533396065654234)) Map(vectorType -> sparse, length -> 25, indices -> List(1, 2, 3, 4, 5, 8, 9, 11, 13, 16, 17, 19, 21, 23), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6808149042250511, 0.3191850957749489)) Map(vectorType -> sparse, length -> 25, indices -> List(1, 2, 3, 4, 5, 8, 9, 11, 13, 16, 17, 19, 21, 23), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 1.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6808149042250511, 0.3191850957749489)) Map(vectorType -> sparse, length -> 25, indices -> List(1, 2, 3, 4, 5, 8, 9, 11, 13, 16, 17, 19, 21, 23), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 1.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6808149042250511, 0.3191850957749489)) Map(vectorType -> sparse, length -> 25, indices -> List(1, 2, 3, 4, 5, 8, 9, 11, 14, 16, 18, 20), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.76951316112486, 0.23048683887514)) Map(vectorType -> sparse, length -> 25, indices -> List(1, 2, 3, 4, 5, 8, 9, 12, 13, 15, 17, 19, 21), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6836153978470328, 0.31638460215296715)) Map(vectorType -> sparse, length -> 25, indices -> List(1, 2, 3, 4, 5, 8, 10, 11, 13, 15, 17, 19, 21), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7019160095942107, 0.2980839904057892

In [0]:
display(pipelineModel.stages[-1], predDF.drop("prediction", "rawPrediction", "probability"), "ROC")


False Positive Rate True Positive Rate Threshold 0.0 0.0 0.4681819943650173 0.0 0.02857142857142857 0.4681819943650173 0.0 0.05714285714285714 0.4542197723393274 0.0 0.08571428571428572 0.45000294406595176 0.0 0.11428571428571428 0.44659417375206845 0.015873015873015872 0.11428571428571428 0.4382761692068984 0.015873015873015872 0.14285714285714285 0.43805357093467334 0.015873015873015872 0.17142857142857143 0.4310060372956718 0.015873015873015872 0.2 0.4280056546266384 0.015873015873015872 0.22857142857142856 0.42267669314547585 0.031746031746031744 0.22857142857142856 0.41533384346017566 0.047619047619047616 0.22857142857142856 0.4079759235207081 0.047619047619047616 0.2571428571428571 0.3986243112933233 0.047619047619047616 0.2857142857142857 0.39381680908967265 0.06349206349206349 0.2857142857142857 0.3937397008383269 0.06349206349206349 0.3142857142857143 0.39058223306837314 0.06349206349206349 0.34285714285714286 0.3832588305928245 0.07936507936507936 0.34285714285714286 0.3797517550230297 0.07936507936507936 0.37142857142857144 0.37863704127920106 0.07936507936507936 0.4 0.3785971122580727 0.07936507936507936 0.42857142857142855 0.37796435392702066 0.09523809523809523 0.42857142857142855 0.3764470023494362 0.1111111111111111 0.42857142857142855 0.37572038866357294 0.12698412698412698 0.42857142857142855 0.3732199568682466 0.12698412698412698 0.45714285714285713 0.3724947735276434 0.12698412698412698 0.4857142857142857 0.37081037242785675 0.14285714285714285 0.4857142857142857 0.35874640692873083 0.15873015873015872 0.4857142857142857 0.3561501133850058 0.15873015873015872 0.5142857142857142 0.353411615146324 0.15873015873015872 0.5428571428571428 0.3527998857370941 0.15873015873015872 0.5714285714285714 0.3517877866621798 0.15873015873015872 0.6 0.3472574152509029 0.15873015873015872 0.6285714285714286 0.3413822703244763 0.15873015873015872 0.6571428571428571 0.3373824215190142 0.15873015873015872 0.6857142857142857 0.33736187037189835 0.15873015873015872 0.7142857142857143 0.3344755477285716 0.15873015873015872 0.7428571428571429 0.33152245140696757 0.1746031746031746 0.7428571428571429 0.3262624968376596 0.1746031746031746 0.7714285714285715 0.3191850957749489 0.19047619047619047 0.7714285714285715 0.3185479482588024 0.19047619047619047 0.8 0.31229252126716456 0.20634920634920634 0.8 0.3037692147833929 0.2222222222222222 0.8 0.2924766931489994 0.2222222222222222 0.8285714285714286 0.2899563664019542 0.2222222222222222 0.8571428571428571 0.2827454576212489 0.2222222222222222 0.8857142857142857 0.278039453946329 0.2222222222222222 0.9142857142857143 0.2750004294133508 0.23809523809523808 0.9142857142857143 0.2728840669121396 0.25396825396825395 0.9142857142857143 0.2701830714580542 0.2698412698412698 0.9142857142857143 0.2623092032973394 0.2857142857142857 0.9142857142857143 0.25585793504369925 0.30158730158730157 0.9142857142857143 0.24964509783874 0.31746031746031744 0.9142857142857143 0.2453978080062228 0.3333333333333333 0.9142857142857143 0.24341565836765622 0.3492063492063492 0.9142857142857143 0.2410221975991773 0.36507936507936506 0.9142857142857143 0.24021287920533263 0.38095238095238093 0.9142857142857143 0.23649665274212073 0.3968253968253968 0.9142857142857143 0.23435256761185297 0.4126984126984127 0.9142857142857143 0.23099377974831203 0.42857142857142855 0.9142857142857143 0.2308461808710358 0.4603174603174603 0.9142857142857143 0.22940750703510226 0.4603174603174603 0.9428571428571428 0.22567919181773477 0.47619047619047616 0.9428571428571428 0.22540572407808812 0.49206349206349204 0.9428571428571428 0.2178973209132813 0.49206349206349204 0.9714285714285714 0.21428321641719938 0.49206349206349204 1.0 0.20977929477416735 0.5079365079365079 1.0 0.20951118796436596 0.5238095238095238 1.0 0.2069046903379279 0.5396825396825397 1.0 0.20651506777473272 0.5555555555555556 1.0 0.20287797045556055 0.5714285714285714 1.0 0.19989970776554722 0.5873015873015873 1.0 0.1977016442032662 0.6031746031746031 1.0 0.197048348

In [0]:
from pyspark.ml.evaluation import BinaryClassificationEvaluator, MulticlassClassificationEvaluator
 
bcEvaluator = BinaryClassificationEvaluator(metricName="areaUnderROC")
print(f"Area under ROC curve: {bcEvaluator.evaluate(predDF)}")
 
mcEvaluator = MulticlassClassificationEvaluator(metricName="accuracy")
print(f"Accuracy: {mcEvaluator.evaluate(predDF)}")

Area under ROC curve: 0.8362026589523512
Accuracy: 0.7330855018587361


In [0]:
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
 
paramGrid = (ParamGridBuilder()
             .addGrid(lr.regParam, [0.01, 0.5, 2.0])
             .addGrid(lr.elasticNetParam, [0.0, 0.5, 1.0])
             .build())

In [0]:
cv = CrossValidator(estimator=pipeline, estimatorParamMaps=paramGrid, evaluator=bcEvaluator, numFolds=3, parallelism = 4)
 
# Run cross validations. This step takes a few minutes and returns the best model found from the cross validation.
cvModel = cv.fit(trainDF)

In [0]:
cvPredDF = cvModel.transform(testDF)
 
# Evaluate the model's performance based on area under the ROC curve and accuracy 
print(f"Area under ROC curve: {bcEvaluator.evaluate(cvPredDF)}")
print(f"Accuracy: {mcEvaluator.evaluate(cvPredDF)}")

Area under ROC curve: 0.8483871696791268
Accuracy: 0.7962825278810409
